In [1]:
import requests 
from bs4 import BeautifulSoup
import pandas as pd
import spacy
from spacy import displacy

In [2]:
url = "https://www.csis.org/analysis/filling-indo-pacific-economic-framework"
response = requests.get(url)

In [3]:
soup=BeautifulSoup(response.content, "html.parser")

In [4]:
print(soup.prettify())

<!DOCTYPE html>
<html class="bg-blue-800" dir="ltr" lang="en" prefix="og: https://ogp.me/ns#">
 <head>
  <meta charset="utf-8"/>
  <meta content="CSIS experts Matthew P. Goodman and Bill Reinsch offer insight on how the Biden administration can fill in the gaps to craft a credible and durable Indo-Pacific economic framework (IPEF)." name="description"/>
  <link href="https://www.csis.org/analysis/filling-indo-pacific-economic-framework" rel="canonical"/>
  <link href="https://csis-website-prod.s3.amazonaws.com/s3fs-public/publication/GettyImages-1184775451.jpg?VersionId=pvxKRzigR8t1SRFt2z5FXB9EoUgd7cJ3" rel="image_src"/>
  <meta content="Filling In the Indo-Pacific Economic Framework" name="citation_title"/>
  <meta content="Matthew P. Goodman" name="citation_author"/>
  <meta content="William Alan Reinsch" name="citation_author"/>
  <meta content="Wed, 01/26/2022 - 12:00" name="citation_publication_date"/>
  <meta content="Filling In the Indo-Pacific Economic Framework" property="og:t

In [5]:
main_content = soup.find('div',{'class':'wysiwyg-wrapper'})
for element in main_content(['aside', 'span']):
    element.decompose()

In [6]:
text_list = []
for paragraph in main_content.find_all('p'):
    paragraph_text = paragraph.get_text(separator=' ', strip=True)
    text_list.append(paragraph_text)

In [7]:
df = pd.DataFrame(text_list, columns=["Paragraph Text"])
df.to_csv('08_paragraphs.csv', index=False)

In [8]:
df

Paragraph Text
0   The Biden administration has presented the out...
1   On October 27, 2021, the Biden White House rel...
2   President Biden also announced that the United...
3   In issuing this statement, the Biden administr...
4   The need for such a strategy is compelling and...
..                                                ...
70  Matthew P. Goodman is senior vice president fo...
71  The authors would like to thank Emily Benson, ...
72  The CSIS Economics Program’s research on the I...
73  This report is produced by the Center for Stra...
74  © 2022 by the Center for Strategic and Interna...

[75 rows x 1 columns]

In [9]:
nlp = spacy.load("en_core_web_sm")

In [10]:
pip install spacy

Note: you may need to restart the kernel to use updated packages.


In [11]:
pip install https://github.com/explosion/spacy-models/releases/download/en_core_web_sm-3.6.0/en_core_web_sm-3.6.0.tar.gz

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 6.4 MB/s eta 0:00:0000:0100:01m
  Preparing metadata (setup.py) ... done
Note: you may need to restart the kernel to use updated packages.


In [12]:
relationship_keywords = {'collaboration', 'cooperation', 'partner', 'engage', 
                         'support', 'fund', 'finance', 'invest', 'develop', 
                         'supply', 'promote', 'transition', 'export', 'agreement', 
                         'interest', 'share', 'enhance', 'effort', 'import'}

In [13]:
def extract_entities_and_relationships(text):
    doc = nlp(text)  # Process text with spaCy
    entities = [(ent.text, ent.label_) for ent in doc.ents if ent.label_ in ['ORG', 'GPE', 'FAC']]

    # Find relationships based on keywords
    relationships = []
    for token in doc:
        if token.lemma_ in relationship_keywords:  # Use lemma_ to check relationship keywords
            subject = [w for w in token.children if w.dep_ == "nsubj"]  # Find subject
            object_ = [w for w in token.children if w.dep_ == "dobj"]  # Find object
            if subject and object_:
                relationships.append((subject[0].text, token.text, object_[0].text))  # (subject, relationship, object)

    return entities, relationships

In [14]:
df['Entities'], df['Relationships'] = zip(*df['Paragraph Text'].apply(extract_entities_and_relationships))

In [15]:
df[['Paragraph Text', 'Entities', 'Relationships']]

Paragraph Text  \
0   The Biden administration has presented the out...   
1   On October 27, 2021, the Biden White House rel...   
2   President Biden also announced that the United...   
3   In issuing this statement, the Biden administr...   
4   The need for such a strategy is compelling and...   
..                                                ...   
70  Matthew P. Goodman is senior vice president fo...   
71  The authors would like to thank Emily Benson, ...   
72  The CSIS Economics Program’s research on the I...   
73  This report is produced by the Center for Stra...   
74  © 2022 by the Center for Strategic and Interna...   

                                             Entities Relationships  
0     [(U.S., GPE), (U.S., GPE), (Indo-Pacific, ORG)]            []  
1                                [(White House, ORG)]            []  
2     [(the United States, GPE), (Indo-Pacific, ORG)]            []  
3                                       [(U.S., GPE)]            []  
4   [(The United States, GPE), (the Indo-Pacific r...            []  
..                                                ...           ...  
70  [(the Center for Strategic and International S...            []  
71             [(the Scholl Chair, ORG), (CSIS, ORG)]            []  
72  [(The CSIS Economics Program’s, ORG), (the Ind...            []  
73  [(the Center for Strategic and International S...            []  
74  [(the Center for Strategic and International S...            []  

[75 rows x 3 columns]

In [16]:
for index, row in df.iterrows():
    print(f"\nParagraph {index + 1}:")
    print(row['Paragraph Text'])

    # Display dependency parsing
    doc = nlp(row['Paragraph Text'])
    sentence_spans = list(doc.sents)
    displacy.render(sentence_spans, style='dep', jupyter=True, options={'compact': True})
    
    # Display named entities
    displacy.render(sentence_spans, style="ent", jupyter=True)
    
    # Print extracted entities and relationships
    print("Entities:", row['Entities'])
    print("Relationships:", row['Relationships'])


Paragraph 1:
The Biden administration has presented the outlines of an “Indo-Pacific economic framework” as the proposed vehicle for U.S. economic engagement in that vital region. A credible and durable economic strategy in Asia is critical to advancing U.S. commercial, diplomatic, and strategic interests. The Biden framework holds promise in this regard but needs to be developed in a way that meets several tests: providing tangible benefits for both Americans and Indo-Pacific partners; advancing binding rules and hard commitments as well as broad principles; being managed in a coherent and coordinated way; and meeting the administration’s commitments to transparency and inclusiveness. This paper offers constructive suggestions on the contents and organization of the administration’s concept with the goal of enhancing its prospects for success.


/Users/loogyee/anaconda3/lib/python3.11/site-packages/spacy/displacy/__init__.py:213: UserWarning: [W006] No entities to visualize found in Doc object. If this is surprising to you, make sure the Doc was processed using a model that supports named entity recognition, and check the `doc.ents` property manually if necessary.
  warnings.warn(Warnings.W006)


Entities: [('U.S.', 'GPE'), ('U.S.', 'GPE'), ('Indo-Pacific', 'ORG')]
Relationships: []

Paragraph 2:
On October 27, 2021, the Biden White House released a short statement offering a readout of the president’s participation in the annual East Asia Summit. It included the following paragraph:


Entities: [('White House', 'ORG')]
Relationships: []

Paragraph 3:
President Biden also announced that the United States will explore with partners the development of an Indo-Pacific economic framework that will define our shared objectives around trade facilitation, standards for the digital economy and technology, supply chain resiliency, decarbonization and clean energy, infrastructure, worker standards, and other areas of shared interest.


Entities: [('the United States', 'GPE'), ('Indo-Pacific', 'ORG')]
Relationships: []

Paragraph 4:
In issuing this statement, the Biden administration was following a traditional pattern for new presidents attending their first round of annual summits in Asia: presenting the contours of a U.S. economic strategy toward that critical region.


...

Entities: [('the Center for Strategic and International Studies', 'FAC'), ('CSIS', 'ORG'), ('Washington', 'GPE'), ('the Scholl Chair', 'ORG'), ('CSIS', 'ORG')]
Relationships: []

Paragraph 72:
The authors would like to thank Emily Benson, associate fellow with the Scholl Chair, for her invaluable research support and contributions. Throughout this project, CSIS scholars received support and input from a wide range of experts and current and former policymakers. Our programs thank them for their counsel.


Entities: [('the Scholl Chair', 'ORG'), ('CSIS', 'ORG')]
Relationships: []

Paragraph 73:
The CSIS Economics Program’s research on the Indo-Pacific Economic Framework is generously supported in part by funding from the Embassy of Japan.


Entities: [('The CSIS Economics Program’s', 'ORG'), ('the Indo-Pacific Economic Framework', 'ORG'), ('the Embassy of Japan', 'ORG')]
Relationships: []

Paragraph 74:
This report is produced by the Center for Strategic and International Studies (CSIS), a private, tax-exempt institution focusing on international public policy issues. Its research is nonpartisan and nonproprietary. CSIS does not take specific policy positions. Accordingly, all views, positions, and conclusions expressed in this publication should be understood to be solely those of the author(s).


Entities: [('the Center for Strategic and International Studies', 'ORG'), ('CSIS', 'ORG'), ('CSIS', 'ORG')]
Relationships: []

Paragraph 75:
© 2022 by the Center for Strategic and International Studies. All rights reserved.


Entities: [('the Center for Strategic and International Studies', 'ORG')]
Relationships: []


In [17]:
entity1_list = []
relationship_list = []
entity2_list = []
date_list = []
money_list = []

In [18]:
# Iterate through each paragraph
for index, row in df.iterrows():
    doc = nlp(row['Paragraph Text'])  # Process the paragraph with spaCy

    for sent in doc.sents:
        # Extract named entities (countries, organizations)
        entities = []
        money_in_sentence = []

        for ent in sent.ents:
            if 'Inititative' in ent.text.lower(): 
                ent = ent._replace(label_='POL')
                entities.append(ent)
            elif ent.label_ in ['GPE', 'ORG', 'POL', 'MONEY']:
                entities.append(ent)

            # Collect monetary amounts
            if ent.label_ == "MONEY":
                money_in_sentence.append(ent.text)
        
        # Look for verbs or specific relationship nouns in the sentence
        verbs = [token for token in sent if token.pos_ == "VERB"]
        keywords_in_sentence = [token.text for token in sent if token.lemma_ in relationship_keywords]
        
        # Extract dates
        dates = [ent.text for ent in sent.ents if ent.label_ == "DATE"]

        # If we find two entities and a relationship keyword, we assume a relationship
        if len(entities) >= 2 and keywords_in_sentence:
            entity1_list.append(entities[0].text)

            # Concatenate the relationship noun and verb (if available) into one string
            relationship_info = keywords_in_sentence[0]
            if verbs:
                relationship_info += " (verb: " + verbs[0].lemma_ + ")"

            relationship_list.append(relationship_info)  # Store concatenated info
            entity2_list.append(entities[1].text)
            date_list.append(dates[0] if dates else "n/a")
            money_list.append(money_in_sentence[0] if money_in_sentence else "n/a")

In [19]:
# DataFrame
relationships_df = pd.DataFrame({
    "Entity1": entity1_list,
    "Relationship": relationship_list,
    "Entity2": entity2_list,
    "Date": date_list,
    "Money": money_list
})

In [20]:
relationships_df

Entity1                Relationship  \
0                            the United States   partners (verb: announce)   
1                            The United States      interests (verb: have)   
2                                      America       partners (verb: view)   
3                                  White House        partner (verb: list)   
4                                         U.S.     interests (verb: argue)   
5                    Trans-Pacific Partnership   agreement (verb: achieve)   
6                                          TPP      partners (verb: bring)   
7                            the United States  agreement (verb: withdraw)   
8             the U.S.-Mexico-Canada Agreement     support (verb: believe)   
9                            The White House’s     develop (verb: develop)   
10                                        IPEF      interests (verb: hold)   
11                                        U.S.    partners (verb: discuss)   
12                                        U.S.   interests (verb: advance)   
13                           The United States       agreement (verb: win)   
14                                        U.S.       partners (verb: move)   
15                                        U.S.     support (verb: propose)   
16                           the United States     agreement (verb: argue)   
17                                     America   agreement (verb: propose)   
18                                        U.S.   interests (verb: advance)   
19                                        IPEF   agreements (verb: ensure)   
20                                        U.S.    interests (verb: ensure)   
21                                        IPEF      supply (verb: present)   
22                           the United States       finance (verb: agree)   
23                          The European Union      funds (verb: announce)   
24                                   Australia      enhancing (verb: mean)   
25                           The United States      agreement (verb: lead)   
26                                         WTO       partners (verb: take)   
27                                        U.S.          fund (verb: exist)   
28                                       USMCA    agreement (verb: accord)   
29                         Department of Labor     agreements (verb: seek)   
30                                        APEC        enhance (verb: give)   
31                           the United States         supply (verb: seek)   
32                                 White House      partners (verb: state)   
33                           the United States       partners (verb: tell)   
34                                     America  agreements (verb: believe)   
35                                        U.S.    partners (verb: include)   
36                                       India    partners (verb: suggest)   
37  the Association of Southeast Asian Nations    enhancing (verb: invite)   
38                                        Laos   developed (verb: develop)   
39                                      Taiwan    partners (verb: consult)   
40                The CSIS Economics Program’s   supported (verb: support)   

                                Entity2            Date         Money  
0                          Indo-Pacific             n/a           n/a  
1               the Indo-Pacific region             n/a           n/a  
2                                  U.S.             n/a           n/a  
3                                  U.S.             n/a           n/a  
4                      the Indo-Pacific             n/a           n/a  
5                                   TPP             n/a           n/a  
6                     the United States             n/a           n/a  
7                                  U.S.      early 2017           n/a  
8                                 USMCA            2019           n/a  
9                                  IPEF   

In [21]:
# Export to csv
relationships_df.to_csv('08_relationships.csv', index=False)